# Search and Visualize Tropical Cyclones from IBTrACS

This notebook allows you to search for tropical cyclones in the IBTrACS (International Best Track Archive for Climate Stewardship) collection by name and visualize their tracks on an interactive map.

We'll use the STAC API at https://montandon-eoapi-stage.ifrc.org/stac/collections/ibtracs-events to search for cyclones by name and retrieve their track data.

## 1. Import Libraries

In [9]:
# Basic libraries
import json
from datetime import datetime

# Visualization libraries
import folium
import pandas as pd
from IPython.display import display, HTML

# STAC libraries
import pystac
import pystac_client
from pystac_monty.extension import MontyExtension

# Import STAC helper functions
import sys
sys.path.append('.')
from stac_helpers import check_stac_api_availability

# Import cyclone visualization helpers
from cyclone_visualization_helpers import (
    search_cyclones_by_name, 
    get_cyclone_by_id, 
    get_cyclone_hazards,
    create_cyclone_map,
    display_cyclone_info,
    search_and_display_cyclone,
    display_cyclone_by_id,
    visualize_cyclone_evolution,
    create_cyclone_evolution_map, 
    create_cyclone_animation
)

## 2. Connect to STAC API

In [10]:
# Define the STAC API endpoint
stac_api_url = "https://montandon-eoapi-stage.ifrc.org/stac"

# Check if the STAC API is available
api_available = check_stac_api_availability(stac_api_url)

if not api_available:
    print("STAC API is not available. Please check the URL or try again later.")
else:
    # Connect to the STAC API using pystac-client
    try:
        catalog = pystac_client.Client.open(stac_api_url)
        print(f"Successfully connected to STAC API at {stac_api_url}")
        
        # Check if the ibtracs-events collection exists
        collections = catalog.get_collections()
        collection_ids = [collection.id for collection in collections]
        
        if "ibtracs-events" in collection_ids:
            print("Found ibtracs-events collection")
        else:
            print("Warning: ibtracs-events collection not found in the catalog")
            
    except Exception as e:
        print(f"Error connecting to STAC API: {e}")
        catalog = None

STAC API is available at https://montandon-eoapi-stage.ifrc.org/stac
Successfully connected to STAC API at https://montandon-eoapi-stage.ifrc.org/stac
Found ibtracs-events collection


## 3. Search for a Cyclone

Enter the name of a tropical cyclone to search for (e.g., "Beryl", "Katrina", "Maria"):

In [11]:
# Example: Search for Hurricane
cyclone_name = "Ida"  # Change this to search for a different cyclone
cyclones_found = search_and_display_cyclone(cyclone_name, catalog)

Found 43 cyclones matching 'Ida':



ID                                 Title  Start Date  \
0   2025029S12076                Tropical Cyclone FAIDA  2025-01-28   
1   2024123S09045               Tropical Cyclone HIDAYA  2024-05-01   
2   2023239N21274               Tropical Cyclone IDALIA  2023-08-26   
3   2021239N17281                  Tropical Cyclone IDA  2021-08-26   
4   2021216N22144                 Tropical Cyclone NIDA  2021-08-03   
5   2020221N13262                Tropical Cyclone ELIDA  2020-08-08   
6   2019063S18038                 Tropical Cyclone IDAI  2019-03-04   
7   2018351S09059               Tropical Cyclone CILIDA  2018-12-16   
8   2016211N11128                 Tropical Cyclone NIDA  2016-07-29   
9   2015259N09336                  Tropical Cyclone IDA  2015-09-15   
10  2014181N17257                Tropical Cyclone ELIDA  2014-06-30   
11  2009325N06148                 Tropical Cyclone NIDA  2009-11-21   
12  2009308N11279                  Tropical Cyclone IDA  2009-11-04   
13  2008194N11266                Tropical Cyclone ELIDA  2008-07-11   
14  2004134N07132                 Tropical Cyclone NIDA  2004-05-13   
15  2002204N12263                Tropical Cyclone ELIDA  2002-07-23   
16  1996244N13257                Tropical Cyclone ELIDA  1996-08-30   
17  1995032S10095                Tropical Cyclone HEIDA  1995-01-31   
18  1992055S11086               Tropical Cyclone FARIDA  1992-02-23   
19  1990177N14257                Tropical Cyclone ELIDA  1990-06-26   
20  1986309N07162                  Tropical Cyclone IDA  1986-11-05   
21  1984180N10258                Tropical Cyclone ELIDA  1984-06-28   
22  1983279N17148                  Tropical Cyclone IDA  1983-10-06   
23  1982031S20048                Tropical Cyclone FRIDA  1982-01-31   
24  1980187N09146                  Tropical Cyclone IDA  1980-07-05   
25  1975309N11154                  Tropical Cyclone IDA  1975-11-05   
26  1975075S14095                 Tropical Cyclone VIDA  1975-03-16   
27  1973354S10098  Tropical Cyclone DALIDA:DEIDRE:DELID  1973-12-20   
28  1972260N16152                  Tropical Cyclone IDA  1972-09-16   
29  1972151S05156                  Tropical Cyclone IDA  1972-05-29   
30  1971046S17158                  Tropical Cyclone IDA  1971-02-15   
31  1969287N11150                  Tropical Cyclone IDA  1969-10-14   
32  1968040S13062                  Tropical Cyclone IDA  1968-02-09   
33  1966261N13158                  Tropical Cyclone IDA  1966-09-18   
34  1964215N07150                  Tropical Cyclone IDA  1964-08-01   
35  1961207N20143                  Tropical Cyclone IDA  1961-07-26   
36  1958263N13148                  Tropical Cyclone IDA  1958-09-20   
37  1954231N10159                  Tropical Cyclone IDA  1954-08-18   
38  1950225N18149                  Tropical Cyclone IDA  1950-08-12   
39  1950221N19124                  Tropical Cyclone IDA  1950-08-09   
40  1947133N16138              Tropical Cyclone BERNIDA  1947-05-13   
41  1946261N11161              Tropical Cyclone QUERIDA  1946-09-18   
42  1945253N08157                  Tropical Cyclone IDA  1945-09-10   

      End Date      Countries  
0   2025-02-05            UNK  
1   2024-05-04            UNK  
2   2023-09-08       MEX, USA  
3   2021-09-04  CUB, USA, CAN  
4   2021-08-08            UNK  
5   2020-08-14            UNK  
6   2019-03-16            UNK  
7   2018-12-28            UNK  
8   2016-08-03            UNK  
9   2015-09-28            UNK  
10  2014-07-02            UNK  
11  2009-12-03            UNK  
12  2009-11-11            UNK  
13  2008-07-21            UNK  
14  2004-05-22            UNK  
15  2002-07-31            UNK  
16  1996-09-06            UNK  
17  1995-02-08            UNK  
18  1992-03-04            UNK  
19  1990-07-02            UNK  
20  1986-11-19            UNK  
21  1984-07-08            UNK  
22  1983-10-13            UNK  
23  1982-02-01            UNK  
24  1980-07-15            UNK  
25  1975-11-15            UNK  
26  1975-03-20            


Enter the ID of the cyclone you want to visualize in the next cell.


## 4. Visualize Cyclone Evolution with Animation

Now let's visualize the evolution of a cyclone over time using the ibtracs-hazards collection. This will show how the cyclone's position and wind speed change over time.

In [13]:
# Example: Visualize the evolution of selected cyclone
if cyclones_found:
    cyclone_id = cyclones_found[3].id
    visualize_cyclone_evolution(cyclone_id, catalog)

Found 77 hazard points for Tropical Cyclone IDA

Creating evolution map...



Creating animation...
